# Fine Tuning roberta model with Twitter Data
*   List item
*   List item





In [23]:
import pandas as pd
import numpy as np
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.model_selection import train_test_split
from sklearn.tree import DecisionTreeClassifier

In [24]:
import re
import string
import nltk
nltk.download('stopwords')
from nltk.stem.snowball import SnowballStemmer

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


### Imports

In [25]:
stemmer = nltk.SnowballStemmer("english")
from nltk.corpus import stopwords
import string
stopword = set(stopwords.words("english"))

In [26]:
df1 = pd.read_csv("twitter_data.csv")
df1 = df1.dropna()
df1.head()

Unnamed: 0  count  hate_speech  offensive_language  neither  class  \
0           0      3            0                   0        3      2   
1           1      3            0                   3        0      1   
2           2      3            0                   3        0      1   
3           3      3            0                   2        1      1   
4           4      6            0                   6        0      1   

                                               tweet  
0  !!! RT @mayasolovely: As a woman you shouldn't...  
1  !!!!! RT @mleew17: boy dats cold...tyga dwn ba...  
2  !!!!!!! RT @UrKindOfBrand Dawg!!!! RT @80sbaby...  
3  !!!!!!!!! RT @C_G_Anderson: @viva_based she lo...  
4  !!!!!!!!!!!!! RT @ShenikaRoberts: The shit you...

#### `.tolist()` converts NumPy arrays into Python lists.

In [27]:
print(df1.columns.tolist())


['Unnamed: 0', 'count', 'hate_speech', 'offensive_language', 'neither', 'class', 'tweet']


- The `.map()` function applies a specified function to an iterable and returns the result.
- We used the `.map` function to assign 0, 1, and 2 to "Hate Speech Detected", "Offensive language detected", and "No hate and -  - offensive speech"

### Preprocess the Labels

In [28]:
df1['labels'] = df1['class'].map({0:"Hate Speech Detected", 1:"Offensive language detected", 2:"No hate and offensive speech"})

# Merging the labels
def unify_labels(row):
    if row['labels'] in ['Hate Speech Detected', 'Offensive language detected']:
        return 'Offensive or Hate Speech'
    else:
        return 'Not Hate'

# Apply this function to the dataset with three labels
df1['labels'] = df1.apply(unify_labels, axis=1)

In [29]:
df1['labels'].info
df1.head()

Unnamed: 0  count  hate_speech  offensive_language  neither  class  \
0           0      3            0                   0        3      2   
1           1      3            0                   3        0      1   
2           2      3            0                   3        0      1   
3           3      3            0                   2        1      1   
4           4      6            0                   6        0      1   

                                               tweet                    labels  
0  !!! RT @mayasolovely: As a woman you shouldn't...                  Not Hate  
1  !!!!! RT @mleew17: boy dats cold...tyga dwn ba...  Offensive or Hate Speech  
2  !!!!!!! RT @UrKindOfBrand Dawg!!!! RT @80sbaby...  Offensive or Hate Speech  
3  !!!!!!!!! RT @C_G_Anderson: @viva_based she lo...  Offensive or Hate Speech  
4  !!!!!!!!!!!!! RT @ShenikaRoberts: The shit you...  Offensive or Hate Speech

### Import the second dataset

### Formated to two tables of tweets and labels

In [30]:
df1 = df1[['tweet', 'labels']]
df1 = df1[['tweet', 'labels']].fillna(0)
df1.head()

tweet                    labels
0  !!! RT @mayasolovely: As a woman you shouldn't...                  Not Hate
1  !!!!! RT @mleew17: boy dats cold...tyga dwn ba...  Offensive or Hate Speech
2  !!!!!!! RT @UrKindOfBrand Dawg!!!! RT @80sbaby...  Offensive or Hate Speech
3  !!!!!!!!! RT @C_G_Anderson: @viva_based she lo...  Offensive or Hate Speech
4  !!!!!!!!!!!!! RT @ShenikaRoberts: The shit you...  Offensive or Hate Speech

In [31]:
def clean(text):
    text = str(text).lower()
    text = re.sub('\[.*?\]', '', text)
    text = re.sub('https?://\S+|www\.\S+', '', text)
    text = re.sub('<.*?>+', '', text)
    text = re.sub('[%s]' % re.escape(string.punctuation), '', text)
    text = re.sub('\n', '', text)
    text = re.sub('\w*\d\w*', "", text)
    text = [word for word in text.split() if word not in stopword]
    text = " ".join(text)
    return text
# Apply cleaning function to the 'tweet' column of both dataframes
df1['tweet'] = df1['tweet'].apply(clean)


In [32]:
df1.head()

tweet                    labels
0  rt mayasolovely woman shouldnt complain cleani...                  Not Hate
1  rt boy dats coldtyga dwn bad cuffin dat hoe place  Offensive or Hate Speech
2  rt urkindofbrand dawg rt ever fuck bitch start...  Offensive or Hate Speech
3           rt cganderson vivabased look like tranny  Offensive or Hate Speech
4  rt shenikaroberts shit hear might true might f...  Offensive or Hate Speech

In [33]:
# Use a pipeline as a high-level helper
from transformers import pipeline

pipe = pipeline("text-classification", model="facebook/roberta-hate-speech-dynabench-r4-target")

In [40]:
# Install necessary libraries
!pip install transformers

import pandas as pd
from sklearn.model_selection import train_test_split
from transformers import TextClassificationPipeline, AutoTokenizer, AutoModelForSequenceClassification
from datasets import Dataset
from transformers import Trainer, TrainingArguments


# Load your CSV file into a pandas DataFrame
data = pd.read_csv("twitter_data.csv")

# Add the 'labels' column to the 'data' DataFrame
data['labels'] = [1 if tweet == 'hate_speech' else 0 for tweet in data['class']]

# Split data into train and validation sets
train_texts, val_texts, train_labels, val_labels = train_test_split(data["tweet"], data["labels"], test_size=0.2, random_state=42)

# Load pre-trained tokenizer and model
tokenizer = AutoTokenizer.from_pretrained("facebook/roberta-hate-speech-dynabench-r4-target")
model = AutoModelForSequenceClassification.from_pretrained("facebook/roberta-hate-speech-dynabench-r4-target")

# Tokenize the input texts
train_encodings = tokenizer(list(train_texts), truncation=True, padding=True)
val_encodings = tokenizer(list(val_texts), truncation=True, padding=True)

# Convert labels to tensors
train_labels = list(train_labels)
val_labels = list(val_labels)

# Create datasets
train_dataset = Dataset.from_dict({"input_ids": train_encodings["input_ids"],
                                   "attention_mask": train_encodings["attention_mask"],
                                   "labels": train_labels})

val_dataset = Dataset.from_dict({"input_ids": val_encodings["input_ids"],
                                 "attention_mask": val_encodings["attention_mask"],
                                 "labels": val_labels})

# Fine-tune the model
model.train(True)

# have to test model

RobertaForSequenceClassification(
  (roberta): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): RobertaEncoder(
      (layer): ModuleList(
        (0-11): 12 x RobertaLayer(
          (attention): RobertaAttention(
            (self): RobertaSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): RobertaSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
             

In [43]:
text_classifier = pipeline("text-classification", model=model, tokenizer=tokenizer)
def test_model():
    while True:
        statement = input("Enter a statement to test (or type 'exit' to quit): ")
        if statement.lower() == 'exit':
            break
        offensive_probabilities = text_classifier(statement)
        print(offensive_probabilities)

In [ ]:
test_model()

Enter a statement to test (or type 'exit' to quit): kill
[{'label': 'nothate', 'score': 0.9961766004562378}]


In [ ]:
from sklearn.metrics import accuracy_score, classification_report

y_pred = clf.predict(X_test)
print(f"Accuracy: {accuracy_score(y_test, y_pred)}")
print(classification_report(y_test, y_pred))